In [1]:
!pip install requests

In [2]:
import requests
import pandas as pd

In [12]:
params = {
    'q': 'tesla', 
    'tweet_mode': 'extended', 
    'lang': 'en', 
    'count': '100'
}

response = requests.get(
    'https://api.twitter.com/1.1/search/tweets.json',
    params = params,
    headers={
        'authorization': 'Bearer '+ 'AAAAAAAAAAAAAAAAAAAAAEBdRgEAAAAA0HWy5oAb5CMm6zvtwUYOnyksd98%3DUTHXRSurMSG3hQBQQewMeUZVyk0MKb7msx35SzQjaVW5y90WBI'
})

In [13]:
response.json()

{'statuses': [{'created_at': 'Mon Jul 12 06:24:32 +0000 2021',
   'id': 1414470714409635845,
   'id_str': '1414470714409635845',
   'full_text': 'RT @GamestonksD: See you on the moon! #Wolfecoin is 30 million supply and live on #Solana! A new memecoin everyone will love :)\n\n#wolfe #wo…',
   'truncated': False,
   'display_text_range': [0, 140],
   'entities': {'hashtags': [{'text': 'Wolfecoin', 'indices': [38, 48]},
     {'text': 'Solana', 'indices': [82, 89]},
     {'text': 'wolfe', 'indices': [129, 135]}],
    'symbols': [],
    'user_mentions': [{'screen_name': 'GamestonksD',
      'name': 'Gamestonks x Wolfecoin (Vevo) Official',
      'id': 1397526330418241543,
      'id_str': '1397526330418241543',
      'indices': [3, 15]}],
    'urls': []},
   'metadata': {'iso_language_code': 'en', 'result_type': 'recent'},
   'source': '<a href="http://twitter.com/download/android" rel="nofollow">Twitter for Android</a>',
   'in_reply_to_status_id': None,
   'in_reply_to_status_id_str': Non

In [62]:
def get_data(tweet):
    data = {
        'id': tweet['id'],
        'created_at': tweet['created_at'],
        'text': tweet['full_text'],
        'user': tweet['user']['name']
    }
    return data

In [26]:
tweets = pd.DataFrame()
for tweet in response.json()['statuses']:
    row = get_data(tweet)
    tweets = tweets.append(row, ignore_index=True)

In [27]:
tweets.head()

created_at                   id  \
0  Mon Jul 12 06:24:32 +0000 2021  1414470714409635845   
1  Mon Jul 12 06:24:31 +0000 2021  1414470709095583745   
2  Mon Jul 12 06:24:20 +0000 2021  1414470664430358535   
3  Mon Jul 12 06:24:19 +0000 2021  1414470660265545731   
4  Mon Jul 12 06:24:17 +0000 2021  1414470649150586881   

                                                text               user  
0  RT @GamestonksD: See you on the moon! #Wolfeco...         Yadi Togel  
1  RT @exerui: if you like albedo and sucrose in ...            boywife  
2  RT @doge1moon_CEO: The future currency of eart...        davidbriane  
3  RT @WSJMag: After the biggest year of her musi...     Gilles🇫🇷Durand  
4  RT @laurenboebert: I’m not the one who blocked...  Wendy_Testaburger

In [14]:
#!pip install flair

ERROR: After October 2020 you may experience errors when installing or updating packages. This is because pip will change the way that it resolves dependency conflicts.

We recommend you use --use-feature=2020-resolver to test your packages with the new resolver before it becomes the default.

huggingface-hub 0.0.13 requires packaging>=20.9, but you'll have packaging 20.4 which is incompatible.
transformers 4.8.2 requires huggingface-hub==0.0.12, but you'll have huggingface-hub 0.0.13 which is incompatible.
konoha 4.6.5 requires requests<3.0.0,>=2.25.1, but you'll have requests 2.24.0 which is incompatible.


  Installing build dependencies: started
  Installing build dependencies: finished with status 'done'
  Getting requirements to build wheel: started
  Getting requirements to build wheel: finished with status 'done'
    Preparing wheel metadata: started
    Preparing wheel metadata: finished with status 'done'
  Created wheel for sqlitedict: filename=sqlitedict-1.7.0-py3-none-any.whl size=14381 sha256=df27d87df364c0927d4c610bcea582c113ca032be1b0f85568d64bca0afabd44
  Stored in directory: c:\users\admin\appdata\local\pip\cache\wheels\92\82\8c\54ef8d8770fd1a80938197e55d3ccd26eccd117f44c58f601b
  Created wheel for mpld3: filename=mpld3-0.3-py3-none-any.whl size=116683 sha256=c9e74f19faebcc1c64263a711f94913d5b53a12f81dab36b8b555ae99c8dcd36
  Stored in directory: c:\users\admin\appdata\local\pip\cache\wheels\3d\9f\9d\d806a20bd97bc7076d724fa3e69fa5be61836ba16b2ffa6126
  Created wheel for segtok: filename=segtok-1.5.10-py3-none-any.whl size=25021 sha256=732c8d4df6238f24a8cdad6f3ecdd2ba03c0bd5

In [16]:
import flair
sentiment_model = flair.models.TextClassifier.load('en-sentiment')

2021-07-12 16:40:55,792 loading file C:\Users\admin\.flair\models\sentiment-en-mix-distillbert_4.pt


In [20]:
sentence = flair.data.Sentence('ungu suck')
sentiment_model.predict(sentence)
sentence

Sentence: "ungu suck"   [− Tokens: 2  − Sentence-Labels: {'label': [NEGATIVE (0.9998)]}]

In [22]:
import re

In [28]:
whitespace = re.compile(r"\s+")
web_address = re.compile(r"(?i)http(s):\/\/[a-z0-9.~_\-\/]+")
tesla = re.compile(r"(?i)@Tesla(?=\b)")
user = re.compile(r"(?i)@[a-z0-9_]+")

In [30]:
def clean(tweet):
    tweet = whitespace.sub(' ', tweet)
    tweet = web_address.sub('', tweet)
    tweet = tesla.sub('Tesla', tweet)
    tweet = user.sub('', tweet)
    return tweet
    

In [31]:
# we will append probability and sentiment preds later
probs = []
sentiments = []

# use regex expressions (in clean function) to clean tweets
tweets['text'] = tweets['text'].apply(clean)

for tweet in tweets['text'].to_list():
    # make prediction
    sentence = flair.data.Sentence(tweet)
    sentiment_model.predict(sentence)
    # extract sentiment prediction
    probs.append(sentence.labels[0].score)  # numerical score 0-1
    sentiments.append(sentence.labels[0].value)  # 'POSITIVE' or 'NEGATIVE'

# add probability and sentiment predictions to tweets dataframe
tweets['probability'] = probs
tweets['sentiment'] = sentiments

In [37]:
tweets

created_at                   id  \
0   Mon Jul 12 06:24:32 +0000 2021  1414470714409635845   
1   Mon Jul 12 06:24:31 +0000 2021  1414470709095583745   
2   Mon Jul 12 06:24:20 +0000 2021  1414470664430358535   
3   Mon Jul 12 06:24:19 +0000 2021  1414470660265545731   
4   Mon Jul 12 06:24:17 +0000 2021  1414470649150586881   
..                             ...                  ...   
95  Mon Jul 12 06:19:51 +0000 2021  1414469535848087556   
96  Mon Jul 12 06:19:49 +0000 2021  1414469526352187393   
97  Mon Jul 12 06:19:44 +0000 2021  1414469507733762050   
98  Mon Jul 12 06:19:43 +0000 2021  1414469503254077443   
99  Mon Jul 12 06:19:40 +0000 2021  1414469489647767555   

                                                 text               user  \
0   RT : See you on the moon! #Wolfecoin is 30 mil...         Yadi Togel   
1   RT : if you like albedo and sucrose in genshin...            boywife   
2   RT : The future currency of earth! 🐕🚀Powered b...        davidbriane   
3   RT : After the biggest year of her music caree...     Gilles🇫🇷Durand   
4   RT : I’m not the one who blocked your abuela f...  Wendy_Testaburger   
..                                                ...                ...   
95                       Tesla CEO please accept doge              MarSS   
96     RT : #ElonMuskJustAnnounced Tesla will accept              🏒𝕿𝖗𝖊𝖘🏒   
97  RT : Happy birthday, #NikolaTesla. In a 1926 i...        Heiko Loewe   
98  RT :  Tesla It will soon capture turn signals,...   Peregrino Sienes   
99  RT : Woah!!! Tesla vision is now capturing and...   Peregrino Sienes   

    probability sentiment  
0      0.999032  POSITIVE  
1      0.987419  POSITIVE  
2      0.998695  POSITIVE  
3      0.999599  NEGATIVE  
4      0.999828  NEGATIVE  
..          ...       ...  
95     0.911295  NEGATIVE  
96     0.901505  POSITIVE  
97     0.890907  POSITIVE  
98     0.999916  POSITIVE  
99     0.991985  POSITIVE  

[100 rows x 6 columns]

In [46]:
from datetime import datetime
datetime.utcnow()

datetime.datetime(2021, 7, 12, 6, 55, 58, 708562)

In [66]:
def get_tweet_data(tweet):
    data = {
        'id': tweet['id'],
        'created_at': tweet['created_at'],
        'text': tweet['text'],
    }
    return data

In [68]:
from datetime import datetime, timedelta
import requests
import pandas as pd

# read bearer token for authentication
BEARER_TOKEN = 'AAAAAAAAAAAAAAAAAAAAAEBdRgEAAAAA0HWy5oAb5CMm6zvtwUYOnyksd98%3DUTHXRSurMSG3hQBQQewMeUZVyk0MKb7msx35SzQjaVW5y90WBI'

# setup the API request
endpoint = 'https://api.twitter.com/2/tweets/search/recent'
headers = {'authorization': f'Bearer {BEARER_TOKEN}'}
params = {
    'query': '(tesla OR tsla OR elon musk) (lang:en)',
    'max_results': '100',
    'tweet.fields': 'created_at,lang'
}

dtformat = '%Y-%m-%dT%H:%M:%SZ'  # the date format string required by twitter

# we use this function to subtract 60 mins from our datetime string
def time_travel(now, mins):
    now = datetime.strptime(now, dtformat)
    back_in_time = now - timedelta(minutes=mins)
    return back_in_time.strftime(dtformat)
    
now = datetime.utcnow() - timedelta(seconds = 10) # get the current datetime, this is our starting point
print(now)
last_week = now - timedelta(days=7)  # datetime one week ago = the finish line
now = now.strftime(dtformat)  # convert now datetime to format for API

df = pd.DataFrame()  # initialize dataframe to store tweets

df = pd.DataFrame()  # initialize dataframe to store tweets
while True:
    if datetime.strptime(now, dtformat) < last_week:
        # if we have reached 7 days ago, break the loop
        break
    pre60 = time_travel(now, 60)  # get 60 minutes before 'now'
    # assign from and to datetime parameters for the API
    params['start_time'] = pre60
    params['end_time'] = now
    response = requests.get(endpoint,
                            params=params,
                            headers=headers)  # send the request
    now = pre60  # move the window 60 minutes earlier
    # iteratively append our tweet data to our dataframe
    print(response.json())
    for tweet in response.json()['data']:
        row = get_tweet_data(tweet)  # we defined this function earlier
        df = df.append(row, ignore_index=True)

2021-07-12 07:02:15.570366
{'data': [{'created_at': '2021-07-12T07:02:09.000Z', 'lang': 'en', 'text': '@arybop @elonmusk @EliBurton_ @Tesla Cool story, hope you don’t get assaulted in your base next time', 'id': '1414480181633462279'}, {'created_at': '2021-07-12T07:02:08.000Z', 'lang': 'en', 'text': '@elonmusk how much likes for a tesla its almost my 18th birthday and I was wanting the safest car out there?', 'id': '1414480176155594755'}, {'created_at': '2021-07-12T07:02:06.000Z', 'lang': 'en', 'text': 'RT @elonmusk: @EliBurton_ @Tesla It will soon capture turn signals, hazards, ambulance/police lights &amp; even hand gestures', 'id': '1414480169876824068'}, {'created_at': '2021-07-12T07:02:03.000Z', 'lang': 'en', 'text': 'RT @AustinTeslaClub: Tesla Vision is 💯 aware… while we check our phones at a red light the safest way is being planned. @tesla @elonmusk #F…', 'id': '1414480156937363457'}, {'created_at': '2021-07-12T07:02:02.000Z', 'lang': 'en', 'text': '@elonmusk @EliBurton_ @Tesla

{'data': [{'lang': 'en', 'text': 'Want to know what #stocks people are tweeting about right now?  🚀 🚀 🚀\n$AMC\n$TSLA\n$SPCE\n$ROKU\n$AAPL\n$AMZN\nCheck out https://t.co/Yq7WY2m4aU to see what else is hot on #twitter\n\n#amc #stockmarket #bitcoin #markets #investing #trading', 'created_at': '2021-07-12T06:02:11.000Z', 'id': '1414465090686959619'}, {'lang': 'en', 'text': 'Confuses as to why a Tesla owner would want to own a Mark X as well.', 'created_at': '2021-07-12T06:02:10.000Z', 'id': '1414465086354337795'}, {'lang': 'en', 'text': 'RT @JCOviedo6: Another Tesla crashes into the back of a truck\n\n$TSLA', 'created_at': '2021-07-12T06:02:07.000Z', 'id': '1414465071393222659'}, {'lang': 'en', 'text': 'Tesla Model 3 now costs less to own than Toyota Camry hybrid - The Driven https://t.co/FTXO3ui7ZX #Tesla #ElonMusk', 'created_at': '2021-07-12T06:02:01.000Z', 'id': '1414465048207048704'}, {'lang': 'en', 'text': '@elonmusk @EliBurton_ @Tesla Take it in to haunted areas', 'created_at': '2021

{'data': [{'text': 'RT @DaSkrambledEgg: A new mens cologne called elon musk \n\n#ElonMuskJustAnnounced', 'id': '1414449996586491904', 'created_at': '2021-07-12T05:02:13.000Z', 'lang': 'en'}, {'text': 'RT @TeslaGong: @_TeslaTom @elonmusk @Tesla @teslaownersau @PhantomLaneFour @TeslaStraya @sydney_ev @DrSallyL Sweet video mate. Loads of inf…', 'id': '1414449989120532480', 'created_at': '2021-07-12T05:02:11.000Z', 'lang': 'en'}, {'text': 'RT @WholeMarsBlog: Someone said they wanted to see FSD Beta 9 in heavy traffic.\n\nHave fun, it’s all yours. $TSLA https://t.co/lhdgaMtGzi', 'id': '1414449986268446723', 'created_at': '2021-07-12T05:02:10.000Z', 'lang': 'en'}, {'text': "RT @agraybee: The way this site naturally assumes South American countries simply don't have any real domestic disputes is beyond paternali…", 'id': '1414449976403324929', 'created_at': '2021-07-12T05:02:08.000Z', 'lang': 'en'}, {'text': 'RT @_TeslaTom: NEW VIDEO: With the recent price drop in Australia, a basic White Tes

{'data': [{'lang': 'en', 'id': '1414434904545271810', 'created_at': '2021-07-12T04:02:14.000Z', 'text': "RT @Tesla_Taylor: This guy couldn't wait until I got home to Cam. #onlyfans #modelsex #models #tesla https://t.co/mdwoK3G1Dx"}, {'lang': 'en', 'id': '1414434878729379844', 'created_at': '2021-07-12T04:02:08.000Z', 'text': 'RT @ShortingIsFun: Don’t charge your #Tesla vehicles during this time period. Unless you’re doing it from your own fossil fuel powered gene…'}, {'lang': 'en', 'id': '1414434849935478784', 'created_at': '2021-07-12T04:02:01.000Z', 'text': 'RT @Investments_CEO: If you want to see Tesla accept $DOGE, \n\nRetweet this post &amp; Comment\n\n “#Doge4Tesla” 🚀 https://t.co/FTYZXikcE4'}, {'lang': 'en', 'id': '1414434848639442946', 'created_at': '2021-07-12T04:02:01.000Z', 'text': 'RT @angieslife: PAY MORE TAXES YALL!!\nhttps://t.co/1NGN0CEzJs'}, {'lang': 'en', 'id': '1414434844805791748', 'created_at': '2021-07-12T04:02:00.000Z', 'text': 'Mr @elonmusk when @Tesla will acce

{'data': [{'id': '1414419798717468676', 'created_at': '2021-07-12T03:02:13.000Z', 'text': '@JHWeissmann Space X is in part an Elon Musk vanity project with grandiose plans of colonizing Mars. But it’s become a huge player with its reusable rockets, especially after the Space Shuttle was retired.', 'lang': 'en'}, {'id': '1414419792346312707', 'created_at': '2021-07-12T03:02:11.000Z', 'text': 'RT @laurenboebert: I’m not the one who blocked your abuela from receiving over $100k. That was all you. \n\nIf that’s how you take care of yo…', 'lang': 'en'}, {'id': '1414419777531965443', 'created_at': '2021-07-12T03:02:08.000Z', 'text': "@Malkavsmarauder @louisdenfir @du_not_disturbb @Angry_Staffer Sure.\n\nhttps://t.co/PMQ2FAoX6W\n\nhttps://t.co/hKkcJlbdFN\n\nhttps://t.co/HsCyIy67o5\n\nhttps://t.co/2lgz7EV0Ex\n\nActually. Search any 'How [company] avoids taxes' or '[billionaire] true tax rate'.\n\nDisclaimer: I'm in favor of space exploration, but that's no excuse for tax evasion.", 'lang': 'en

...

{'data': [{'created_at': '2021-07-05T11:02:10.000Z', 'text': '@DaddyCool___ @drmuizmurad Yes, similar to Tesla tech by one of our own!', 'id': '1412003869580697602', 'lang': 'en'}, {'created_at': '2021-07-05T11:02:10.000Z', 'text': 'Tesla’s entry into the S&amp;P 500 has cost investors tracking or benchmarked against the index of blue-chip US stocks more than $45bn since December https://t.co/S8H1zX5Noc https://t.co/TRPH2DfOsV', 'id': '1412003867634569218', 'lang': 'en'}, {'created_at': '2021-07-05T11:02:09.000Z', 'text': 'RT @teslaownersSV: The possibility with the cybertruck are endless. Expect the unthinkable. I wonder why accessories @tesla @elonmusk will…', 'id': '1412003863683645440', 'lang': 'en'}, {'created_at': '2021-07-05T11:02:05.000Z', 'text': '@TheBlakeCheck @Tesla I don’t understand why.. love my MY', 'id': '1412003848684777473', 'lang': 'en'}, {'created_at': '2021-07-05T11:02:03.000Z', 'text': 'Construction has begun for a new charging site at Cringleford, Cringleford, G

{'data': [{'id': '1411988775018717192', 'lang': 'en', 'created_at': '2021-07-05T10:02:12.000Z', 'text': 'RT @ALLProCrypto: TESLA ACCEPT $DOGE'}, {'id': '1411988770954649602', 'lang': 'en', 'created_at': '2021-07-05T10:02:11.000Z', 'text': '@TeslaStars M3 won’t be the best selling car in July though - due to the well-documented @tesla production and allocation strategy\n\n$TSLAQ 🤡 are gonna be saying there are M3 sales problems in U.K. in July / August 🤦\u200d♂️\n\nI guess that $TSLAQ are (kinda) correct 2 months out of each quarter ! 😆'}, {'id': '1411988769209831426', 'lang': 'en', 'created_at': '2021-07-05T10:02:10.000Z', 'text': 'RT @Teslarati: Elon Musk posts update about the Tesla Cybertruck’s final design -- plus a cool new feature\n\nCredit to @aleks3d_art on IG fo…'}, {'id': '1411988754529767426', 'lang': 'en', 'created_at': '2021-07-05T10:02:07.000Z', 'text': 'RT @CodingMark: 1 Tesla fire is national news\n\n1 Legacy auto fire is 🤷\u200d♂️\n\nTesla is less than 5% of all cars'}

{'data': [{'id': '1411973683443384320', 'created_at': '2021-07-05T09:02:13.000Z', 'text': 'RT @_LittleGecko: wonderful candle🚀🚀🚀🚀🦎🦎🦎we are going to the moon and beyond! @elonmusk @OfficialTravlad @dogecoin @cz_binance @Tesla #BNB…', 'lang': 'en'}, {'id': '1411973659338493959', 'created_at': '2021-07-05T09:02:08.000Z', 'text': 'RT @PredZdravkovic: An immortal tribute to one of the greatest minds in the world @elonmusk the man behind @Tesla @SpaceX @boringcompany…', 'lang': 'en'}, {'id': '1411973650677334018', 'created_at': '2021-07-05T09:02:06.000Z', 'text': '@tesloniq @FenceTesla Just like I believe Tesla car can self drive without crashing into firetrucks😁', 'lang': 'en'}, {'id': '1411973642871791616', 'created_at': '2021-07-05T09:02:04.000Z', 'text': '@CryptoTony__ $AMC $IOST $LSK $ELON $LTC $UPX $BTC $TSLA $DOGE $UPX $BTC $TSLA $DOGE $SHIB $XLM $LTC $APPL $LINK $ETH $BNB $ADA $ETC $XMR $STMX $ZEC $NEO $MATIC $DASH $BTT  $BTG $SC $GRT $XVS $CELO $AMZN $SQ $PYPL\n👇🏻👇🏻\n\nhttps://t.co/

{'errors': [{'parameters': {'start_time': ['2021-07-05T07:02Z']}, 'message': "Invalid 'start_time':'2021-07-05T07:02Z'. 'start_time' must be on or after 2021-07-05T07:04Z"}], 'title': 'Invalid Request', 'detail': 'One or more parameters to your request was invalid.', 'type': 'https://api.twitter.com/2/problems/invalid-request'}


KeyError: 'data'

In [69]:
df.head()

created_at                   id  \
0  2021-07-12T07:02:09.000Z  1414480181633462279   
1  2021-07-12T07:02:08.000Z  1414480176155594755   
2  2021-07-12T07:02:06.000Z  1414480169876824068   
3  2021-07-12T07:02:03.000Z  1414480156937363457   
4  2021-07-12T07:02:02.000Z  1414480149676838913   

                                                text  
0  @arybop @elonmusk @EliBurton_ @Tesla Cool stor...  
1  @elonmusk how much likes for a tesla its almos...  
2  RT @elonmusk: @EliBurton_ @Tesla It will soon ...  
3  RT @AustinTeslaClub: Tesla Vision is 💯 aware… ...  
4  @elonmusk @EliBurton_ @Tesla Will you enter MI...

In [79]:
type(df['created_at'][1])

str

In [73]:
#!pip install yfinance
import yfinance as yf

In [84]:
tsla = yf.Ticker("TSLA")
tsla_stock = tsla.history(
    start=(df['created_at'].min()[0:10]),
    end=df['created_at'].max()[0:10],
    interval='60m'
).reset_index()

In [85]:
tsla_stock

Datetime        Open        High         Low       Close  \
0  2021-07-06 09:30:00-04:00  683.500000  683.960022  657.770020  665.169983   
1  2021-07-06 10:30:00-04:00  665.080017  667.500000  660.800110  661.799988   
2  2021-07-06 11:30:00-04:00  661.947510  663.146179  651.400208  654.570007   
3  2021-07-06 12:30:00-04:00  654.400024  657.840027  652.340027  657.206726   
4  2021-07-06 13:30:00-04:00  657.114990  658.400024  654.820007  656.309998   
5  2021-07-06 14:30:00-04:00  656.200012  658.299988  653.765015  657.200012   
6  2021-07-06 15:30:00-04:00  657.349976  660.790283  656.429993  659.489990   
7  2021-07-07 09:30:00-04:00  664.270020  665.700012  643.390015  643.960022   
8  2021-07-07 10:30:00-04:00  643.857483  645.759521  638.320007  644.471497   
9  2021-07-07 11:30:00-04:00  644.260010  648.900024  641.559998  645.619995   
10 2021-07-07 12:30:00-04:00  645.539978  647.450012  642.380127  644.669983   
11 2021-07-07 13:30:00-04:00  644.469971  648.710022  643.321411  645.770020   
12 2021-07-07 14:30:00-04:00  645.599976  646.929993  642.700012  644.614990   
13 2021-07-07 15:30:00-04:00  644.540100  646.500000  643.599976  644.849976   
14 2021-07-08 09:30:00-04:00  628.369995  640.274780  620.460022  639.559998   
15 2021-07-08 10:30:00-04:00  639.320007  641.799988  634.580017  639.000000   
16 2021-07-08 11:30:00-04:00  639.000000  646.286011  636.500000  645.290894   
17 2021-07-08 12:30:00-04:00  645.435974  650.719971  644.900024  649.650024   
18 2021-07-08 13:30:00-04:00  649.690918  651.789978  646.250000  647.683411   
19 2021-07-08 14:30:00-04:00  647.544983  651.309998  646.160095  647.679993   
20 2021-07-08 15:30:00-04:00  647.599976  654.429993  647.030029  653.309998   
21 2021-07-09 09:30:00-04:00  655.549988  656.690002  647.453125  650.905029   
22 2021-07-09 10:30:00-04:00  650.940002  653.539978  648.479980  652.075012   
23 2021-07-09 11:30:00-04:00  652.150024  656.690002  650.361389  655.684998   
24 2021-07-09 12:30:00-04:00  655.619995  658.909973  653.559998  654.609985   
25 2021-07-09 13:30:00-04:00  654.580017  655.399902  652.849976  654.670105   
26 2021-07-09 14:30:00-04:00  654.900024  656.250000  653.500000  655.153687   
27 2021-07-09 15:30:00-04:00  655.070007  657.619995  655.070007  656.989990   

     Volume  Dividends  Stock Splits  
0   8417055          0             0  
1   3268730          0             0  
2   3504500          0             0  
3   2033090          0             0  
4   1356744          0             0  
5   1722202          0             0  
6   1753385          0             0  
7   6533473          0             0  
8   3907527          0             0  
9   2056799          0             0  
10  1370674          0             0  
11  1603200          0             0  
12  1527975          0             0  
13  1338925          0             0  
14  8298995          0             0  
15  3135138          0             0  
16  2657097          0             0  
17  2427912          0             0  
18  1760316          0             0  
19  1468725          0             0  
20  2003744          0             0  
21  5700063          0             0  
22  2211296          0             0  
23  2008134          0             0  
24  2375168          0             0  
25  1397758          0             0  
26  1661450          0             0  
27  1678686          0             0